<a href="https://colab.research.google.com/github/Brandi-Kinard/opencv-motion-detection/blob/main/Motion_Detection_in_Videos.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

<h1 style="font-size:30px;">Motion Detection in Videos</h1>

This notebook showcases the process of detecting motion in videos featuring foreground moving objects. The OpenCV techniques utilized in this notebook consist of:

* Employing a [**`background subtraction model`**](https://docs.opencv.org/3.4/d1/dc5/tutorial_background_subtraction.html) to separate moving objects in the foreground, resulting in a foreground mask.
* Applying a technique known as "[**`erosion`**](https://docs.opencv.org/3.4/db/df6/tutorial_erosion_dilatation.html)" to reduce noise within the foreground mask.

Here's the workflow:

* Create a statistical model of the background scene using **`createBackgroundSubtractorKNN()`**
* For each video frame:
    * Compare the current frame with the background model to create a foreground mask using the **`apply()`** method
    * Apply erosion to the foreground mask to reduce noise using **`erode()`**
    * Find the bounding rectangle that encompasses all the non-zero points in the foreground mask using  **`boundingRect()`**


# 1. Setup and Imports

Ensure that the notebook imports all necessary libraries and configures the environment for video processing.

In [ ]:
# Install necessary libraries
!pip install opencv-python==4.8.0.76
!pip install moviepy==0.2.3.5
!pip install imageio==2.4.1

import cv2
import numpy as np
from matplotlib import pyplot as plt


# 2. Previewing the Video File

In [ ]:
from moviepy.editor import VideoFileClip

input_video = './home_dog.mp4'

# Load the video for playback.
clip = VideoFileClip(input_video)
clip.ipython_display(width = 800)

pygame 2.5.2 (SDL 2.28.2, Python 3.10.12)
Hello from the pygame community. https://www.pygame.org/contribute.html


100%|██████████| 1055/1055 [00:13<00:00, 79.08it/s]


# 3. Create Video Capture
Handle video capture and ensure the video is loaded correctly.

In [ ]:
# Create the video capture object
video_cap = cv2.VideoCapture(input_video)
if not video_cap.isOpened():
    print('Unable to open: ' + input_video)

# 4. Create Video Writer Objects

In [ ]:
# Retrieve video frame properties.
frame_w = int(video_cap.get(cv2.CAP_PROP_FRAME_WIDTH)) // 2
frame_h = int(video_cap.get(cv2.CAP_PROP_FRAME_HEIGHT)) // 2
fps = int(video_cap.get(cv2.CAP_PROP_FPS))

# Create the video writer object.
video_out = cv2.VideoWriter('output_eroded.mp4', cv2.VideoWriter_fourcc(*'mp4v'), fps, (frame_w, frame_h))

# 5. Background Subtraction and Frame Processing
Use background subtraction method provided by OpenCV, applying frame differencing, thresholding, and erosion.

### <font style="color:rgb(50,120,230)">Create background subtraction object</font>

In [ ]:
bg_sub = cv2.createBackgroundSubtractorKNN(history = 6000) # Background Subtractor

### <font style="color:rgb(50,120,230)">Process video frames</font>

In [ ]:
ksize = (5, 5)  # Kernel size for the erosion
red = (0, 0, 255)

# Read one frame at a time.
while True:
    ret, frame = video_cap.read()
    if not ret:
        break

    # Apply background subtraction
    fg_mask = bg_sub.apply(frame)

    # Apply erosion to reduce noise and improve the mask
    fg_mask_erode = cv2.erode(fg_mask, np.ones(ksize, np.uint8))

    # Motion area based on foreground mask with erosion
    motion_area_erode = cv2.findNonZero(fg_mask_erode)

    # Draw bounding box for motion area based on foreground mask with erosion
    if motion_area_erode is not None:
        xe, ye, we, he = cv2.boundingRect(motion_area_erode)
        cv2.rectangle(frame, (xe, ye), (xe + we, ye + he), red, thickness=6)

    # Resize the frame for consistent output dimensions or viewing convenience
    frame = cv2.resize(frame, (frame_w, frame_h))

    # Write the frame to the output video file
    video_out.write(frame)

video_cap.release()
video_out.release()

# 6. Load the Newly Created Video To Confirm Creation

In [ ]:
output_video = './output_eroded.mp4'

# Load the video for playback.
clip = VideoFileClip(output_video)
clip.ipython_display(width = 800)


100%|██████████| 1055/1055 [00:01<00:00, 584.86it/s]
